Preprocess data

In [1]:
import pandas as pd
from tqdm import tqdm
import csv

In [2]:
brandbankExtract = r'C:\Users\admin_1878\Documents\Brandbank Data\Extracted Data\Brandbank Extract.csv'

In [3]:
df = pd.read_csv(brandbankExtract)
df=df.fillna('')
df['text'] = df[[
    'description',
    'allergyAdvice',
    'recycling',
    'recycling_other',
    'brands',
    'marketing',
    'ingredients',
    'features',
    'storage',
    'preserves']].agg(' '.join, axis=1)
df=df.drop(['name'
    ,'pl2','pl3',
    'description',
    'allergyAdvice',
    'recycling',
    'recycling_other',
    'brands',
    'marketing',
    'ingredients',
    'features',
    'storage',
    'preserves'],axis=1)
df.rename({'pl1':'category'},axis=1, inplace=True)
df.drop(df[df['category'] =='Kruidenierswaren'].index, inplace=True)#onyl 1 example of this so dropping for simplicity
df['category'] = df['category'].str.replace(" ", "_")
df = df[df['category'] != '']
df = df[df['category'] != 'Unallocated']
df['text'] = df['text'].str.lower()
df.head()

category                                              text
0       Dairy_&_Bread  waitrose fig & raisin loaf 400g    waitrose     
1                Deli        wr gingerbread biscuit chick each         
2       Dairy_&_Bread   waitrose petit parisienne 290g    waitrose     
3  Fruit_&_Vegetables    waitrose loose yellow peppers    waitrose     
4  Fruit_&_Vegetables                asda pink lady apples    asda

RAKE_NLTK

In [4]:
from rake_nltk import Rake
import nltk

In [5]:
#nltk.download('stopwords') #Only needs to be run once to download stop words

In [6]:
def get_num_words(row):
    return len(str(row['Phrase']).split())

def get_perc_phrase(row,total):
    return (float(row['Score'])/total*100)

In [7]:
def get_Rake_phrases(df):
    r = Rake()
    r.extract_keywords_from_sentences(df['text'])
    phrases=r.get_ranked_phrases_with_scores()
    df = pd.DataFrame(phrases, columns = ['Rank', 'Phrase'])
    df['Phrase'] = df['Phrase'].str.strip()
    phrase_counts = df['Phrase'].value_counts()
    phrase_counts = phrase_counts.reset_index()
    phrase_counts.columns=['Phrase','Score']
    phrase_counts['Length'] = phrase_counts.apply (lambda row: get_num_words(row), axis=1)
    phrase_counts=phrase_counts.loc[phrase_counts['Length'] <=6]
    total = float(phrase_counts['Score'].sum())
    phrase_counts['Perc'] = phrase_counts.apply (lambda row: get_perc_phrase(row,total), axis=1)
    return phrase_counts

In [8]:
df_raked = get_Rake_phrases(df)
#phrase_counts.to_csv(r'C:\Users\Clamfighter\Documents\GitHub\NLP\Impact Score Key Phrase\Extracted Phrases\Rake NLTK\Brandbank Latest Phrase Extraction.csv',index = False)

In [9]:
phrase_count=[]

df_phraseCount = df_raked.loc[df_raked['Score'] != 1] #filters Score of 1 out. will be added back in later
phrases = df_phraseCount['Phrase']
text = df['text']
for phrase in phrases: #find number of phrases for all strings
    phrase_count.append(sum(phrase in s for s in text))
    print (phrase)
phrase_count

contains
free
may contain
suitable
sugar
salt
milk
water
wheat
vegetarians
made
soya
100
wheat flour
5
1
artificial colours
iron
plastic
citric acid
flavours
niacin
2
nuts
day
0
aqua
preservatives
widely recycled
use
emulsifier
colour
home freezing
skin
keep refrigerated
parfum
rapeseed oil
sulphites
calcium carbonate
cocoa butter
peg
glycerin
vegans
limonene
4
perfect
3
recycle
peanuts
cocoa mass
gluten
’
flavourings
acidity regulator
linalool
glucose syrup
product
eggs
preservative
gluten free
enjoy
sainsbury
source
sunflower oil
mono
non
minerals
home
protein
dextrose
p
fibre
high
colours
love
easy
mustard
sesame
time
spices
ready
palm oil
flavouring
tray
calcium
diglycerides
fish
make
concentrate
world
yeast
cornflour
citronellol
taste
6
recyclable
l
hexyl cinnamal
phenoxyethanol
sodium benzoate
card
lactose
need
stabiliser
hair
rich
oats
yeast extract
vitamin
minimum
black pepper
sodium chloride
fragrance
palm
skimmed milk powder
acid
meat
one
animal derivatives
co
added sugar
pot

france
pro
potassium nitrate
petrolatum
flavour enhancer
11
menthol
polyglyceryl
grape
sunflower lecithin
growth
niacinamide
aluminum chlorohydrate
maize flour
liquid
day long
right
nation
iron oxides
caramelised sugar syrup
got
tiredness
build
pop
mineral oil
benzophenone
fennel
cocoa solids
eau
hellmann
effective
durum wheat semolina
name
natural sources
unique odourclear technology
vets
sodium salicylate
pineapple
works
low fat
milk chocolate contains
milk chocolate contains milk solids 14
environment
sugar free
smoked paprika
spice extracts
12 hours
creating
experience
seasoning
years
babies
yogurt
side
aloe vera
24 hours
2 minutes
sultanas
happy
delicate
100 stearate
better
oven
cats
persea gratissima oil
full range
reduction
last
store
16
added preservatives
sugars
small
amyl cinnamal
including 4
trust
cocamide mea
follow
beautiful
palate
rest
butyrospermum parkii butter
extract
cashew nuts
breakfast
edta
dark chocolate
fast
ever
help keep
large supermarket
sweetness
canned
pork 

pork gelatine
refresh
17 %)
healthy digestion
five
tastes
crispy
walkers
features
hexadimethrine chloride
lots
covered
drying
gum disease
pantene pro
dha
vegans suitable
feminine care
perfect gift
essential waitrose
semi
ethylparaben
essential
triphosphates
vit
cetyl esters
used 12 hours
grey coverage
natural vanilla extract
delicious flavours
lightweight
truly cleans away tough lingering odours
perspirant
soups
tip
cola
thiamin ), salt
nano
glyceryl oleate
adult dogs
father
british beef
almond
pumpkin seeds
dried egg white
blueberry
potassium iodide
softer
specifically designed
car freshener
phthalates
generations
palm kernel
stronger
dishwasher safe
fight
milk ), lactose
arginine
types
essential oils
everyday use
layer
amount
ease
cracked black pepper
ci 74160
lime juice
sodium acetate
chips
contains tray
limescale
cold wash
cranberry
party
future
zinc sulphate
proof
dijon mustard
leaf extract
ph balanced
whole grain
copernicia cerifera cera
kick
boost
simmondsia chinensis seed oil
c

beetroot
deserve
collection
6 months
asda butcher
wipe
glyceryl stearate citrate
content
snap
yet
removing surface stains
150 distearate
gellan gum
soon
oleyl alcohol
vegetable stock
hexadecene copolymer
online panel
toast
cruelty free international
british chicken
e412
lactobacillus acidophilus
dream
abv
sprinkle
girl
disodium stearoyl glutamate
combine
soothes
flammable
7 days
palm kernel ), cocoa butter
far
high quality fragrances p
1937
seal
epa
trigger
white chocolate
poppy seeds
bay leaf
natural propellant
relieve
extra
pvp
wheatflour
hyaluronic acid
goes
deodorant
carry
full flavour
sun exposure
vegetarian keep refrigerated
nicotine
line
first time
average
walk
quinoa
chlorphenesin
dog needs
allow
comfortable fit
cocktails
vision
citrus fibre
whey protein concentrate
healthier
red onion
shaves
adjustable scent intensity
sold separately
dried beet pulp
understand
arabica
see leaflet
moist
pasteurised free range egg yolk
thought
glyceryl stearate se
step
prevent
healthy vitality
w

flake
growing
core
packet responsibly
body ’
cultures
moisturise
richness
b1 ), niacin
named
science
money
thinner
sodium stearoyl glutamate
return
potassium carbonate
cereal
knorr
coated
desserts
stabilizer
bars
get used
kale
soya lecithin ), salt
contains asda fortified wheat flour
whisky
ci 77266
temperature
elasticity
helps protect
space
burgers
releases
maltitol
kitten
magnesium sulfate
soya free
e322
flash
artificial additives
harvest
coconut cream
wet hair
animal fat
winemakers
full bodied
b1
ammonium bicarbonate ), salt
personal care
kitkat chunky
modified cornflour
hot water
https :// www
tooth decay
e331
smoked salt
1 1
whey solids
febreze products
ages
worked
blue 1 lake
2 1
reuse
ci 16035
carrot concentrate
lauraldehyde
shea fat
daily brushing
3 years
bergamot
fed
fat reduced cocoa
body wash
tert
unwrapping
03
behenyl alcohol
yellow stains
peel oil
cocoa solids 30
cornwall
arabica coffee
allows
colmans
8 %), sugar
cheeses
china
selenium
act
raw
finds
sustainability througho

...

time keeper red 75cl sulphur dioxide
nib means hours
zingy mix
refreshing smooth orange juice
acana lavender carpet
collecting play
correct english
shattering truth
function allows
89 %), spirit vinegar
equipment required
navy sainsbury
throttle powerhouse
acidity regulator lactic acid stuffed
soy nuggets
instant favourite
whilst minimising wear
pitted prunes
sodium nitrite ), british butter
phosphates ), glucose syrup
recycle sensations first ...
e270 ), natural colour
³clinical study
manoeuverability p
forcing margaret
lasting colour result
affectionately named
equals survival
instant cooling
99 celery
natural foods peanuts
water ), natural cane sugar
producing top quality square sausage
crisp chocolate flavour layers
5 caramel rice squares 150g eggs
paprika extract ), tomato
exceptional shine results
commonly eaten indian food
5 %*
lovely mix
5 %), peach flavouring
9 %), rice starch
tragedy struck
elsa feared
start silencing
german commander general breugal becomes suspicious
cornis

soy protein ), acid
three including best picture
salt ), celery salt
beetroot juice powder ), pimento
dips – enjoy
snak source
styrian goldings providing late aromas
deeply penetrate
find interesting
widely recycled waitrose tomatoes grown
fully recyclable westland benefits 1
fatty acids ), cauliflower
tongue tingling ginger
contains nissin
glycerol ), flavouring sweet
l c32837
causes bad breath 4
blue bayou
supports natural skin healing
terroirs alizarine
terroirs albaneve
blue yoshi
hit itv2 show
flagship wwe franchise
natural origin sparkling orange beverage
revlon magnifying lash brush
fed organic bone broth 324g recycle
try glazed
contains riya
min value
world renowned
l d16627416
canadian lobster
adding initials
bontan remix
often seen
extra short length setting
crispy whole onion rings 375g wheat
butter pastry case ...
contains celery ), fat powder
e471 ), golden syrup
op british pickled beetroot 150g co
gel clings
k ), natural flavourings
wings 230g barley
mushroom extract japa

rather delicious vodka fizz
complete original
fruit burst flavor toothpaste
double cream chocolate ganache
get social
51 %), palm oil
diphosphates ), vanilla extract
ci 75470 ), fd
thus ensuring
chives 200g waitrose
make lovely gifts
death zone
contains milk )] baked
number one bestselling series
strathmore strathmore carbonated spring water
mushroom pie 650g barley
extract milk
e250 )), sliced leeks
often available
sodium benzoate ), foaming agent
use panadol period pain
water based colour
form initials
never worry
new year ’
garlic farm tasting notes
winning olive oil producers
potassium sorbate developed
one last dance ... lily
dire poverty
rapeseed ), red onion
lynx spray deodorant
aminopyridine hcl
rapeseed oil ), tomato paste
ideal thickness
racetrack gangs
caramelised sugar ), water
light reflecting properties
better health families campaign 1
sure women tropical anti
soy powder
apple pieces *, coconut chips
e330 ), milk protein
almond 400g almonds
original dopiaza sauce 450g gl

menthol 0
allows storytelling skills
anthropomorphic ninjutsu
sodium metabisulphite )], paprika
1 conc
deemed physically unfit
cook chicken fillets
deliciously different way
depth reporting
cayenne pepper )), onions
8 paper plates sainsbury
perfect roast vegetables
rye ), dried garlic
44 %), fortified wheat flour
help cut food waste
contains thatchers thatchers rosé
black interdesign
synthetic pesticides
finest peach
flavouring packed using british cream
bronze award winner 2019
jane harper _________
babies enjoy
blocking
5 %), whole grain barley flour
tumble fresh passionfruit pulp
op sweet
enchant
including calcium ), milk
polysorbate 80 ), flavouring
ingredients medicated relief
monsters university
nut combos sea salt
mailbox sized pack p
1 minute stirring continuously
gluten ), palm oil
carb killa ® shake
bold birthday loot bags featuring
citric acid ], glucose
facilities exist dp contains acetic acid
op information
3 %), soya protein
30 %), corn fibre
hc
submarine
shattering concl

[46566,
 28091,
 14558,
 32327,
 33710,
 30064,
 24913,
 32879,
 18937,
 19380,
 17271,
 14045,
 19305,
 12185,
 60337,
 69585,
 11014,
 11646,
 9490,
 15215,
 15166,
 9424,
 58041,
 12058,
 16578,
 77855,
 9008,
 10239,
 12937,
 19992,
 11161,
 27689,
 7826,
 8550,
 14309,
 7054,
 9215,
 6867,
 6744,
 5069,
 4280,
 7452,
 7201,
 6440,
 43863,
 14535,
 44832,
 26704,
 5308,
 4691,
 13069,
 4196,
 11871,
 9098,
 6022,
 6752,
 9091,
 9353,
 17189,
 6271,
 7774,
 4705,
 9541,
 7125,
 5219,
 10649,
 3803,
 15483,
 10848,
 5792,
 103643,
 6501,
 11716,
 16087,
 10026,
 7220,
 4451,
 4553,
 9733,
 5295,
 5171,
 5415,
 22813,
 5266,
 12950,
 3017,
 4421,
 9725,
 11328,
 5503,
 9846,
 4612,
 3706,
 11589,
 32152,
 10579,
 110538,
 3571,
 3512,
 3894,
 6532,
 4007,
 6597,
 8392,
 3981,
 10154,
 3346,
 4598,
 8260,
 2725,
 5427,
 3489,
 5721,
 12830,
 4067,
 28359,
 4632,
 30091,
 1572,
 91963,
 3208,
 5299,
 3839,
 13329,
 8933,
 5564,
 37226,
 6875,
 8309,
 17319,
 6401,
 27486,
 5096,
 3150,


In [10]:
df_phraseCount['Count'] = phrase_count
df_phraseCount.drop(['Score','Length','Perc'],axis=1, inplace=True)
df_out = df_raked.merge(df_phraseCount, on='Phrase', how='left')
df_out.fillna(1,inplace=True)
df_out

C:\Users\admin_1878\AppData\Local\Temp\ipykernel_11008\2573982755.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_phraseCount['Count'] = phrase_count
C:\Users\admin_1878\AppData\Local\Temp\ipykernel_11008\2573982755.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_phraseCount.drop(['Score','Length','Perc'],axis=1, inplace=True)


Phrase  Score  Length      Perc    Count
0                                  contains  46090       1  1.043119  46566.0
1                                      free  27964       1  0.632888  28091.0
2                               may contain  27856       2  0.630443  14558.0
3                                  suitable  26888       1  0.608535  32327.0
4                                     sugar  25511       1  0.577371  33710.0
...                                     ...    ...     ...       ...      ...
500458                  best fighting units      1       3  0.000023      1.0
500459  piers morgan unbranded piers morgan      1       5  0.000023      1.0
500460         extremely perilous christmas      1       3  0.000023      1.0
500461                    trifles unbranded      1       2  0.000023      1.0
500462                holly smale unbranded      1       3  0.000023      1.0

[500463 rows x 5 columns]

In [1]:
df_out.to_csv(r'out_lower.csv',index = False)

NameError: name 'df_out' is not defined